# Input Source Codes

In [1]:
import os
import re
import nltk
import pandas as pd
import numpy as np
nltk.download('punkt')

from nltk.tokenize import word_tokenize
from sklearn.metrics import accuracy_score,precision_score,recall_score,f1_score

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\haydariday\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
source_codes = []
filenames = []
LOC = []
n_LOC = []
filenames_without_extension = []


tags_count = {}
function_dict = {}
function_token = {}

stop_condition = ('for', 'if', 'else', 'while','switch')

tags_count['LOC'] = 0
tags_count['SLOC'] = 0
tags_count['O'] = 0
tags_count['C'] = 0
tags_count['M'] = 0
tags_count['N'] = 0


sc_directory = 'Source_codes/apache/'
py_directory = 'apache.xls'

In [3]:
%%time

filenames = os.listdir(sc_directory)
for name in filenames :
    i = name.replace('.c','')
    filenames_without_extension.append(i)
filenames

Wall time: 0 ns


['http_core.c', 'mod_cache.c', 'mod_file_cache.c']

In [4]:
%%time
i = 0
for files in filenames :
    function_dict[filenames_without_extension[i]] = {}
    with open(sc_directory+files,'r') as fh :
        source_codes.append([filenames_without_extension[i],fh.readlines()])
    i += 1

Wall time: 1e+03 µs


In [5]:
%%time

for source_code in source_codes :
    i = 0
    for baris in source_code :
        if not (i % 2 == 0) :
            LOC.append(len(baris))
            tags_count['LOC'] += len(baris)
        i+=1
LOC

Wall time: 0 ns


[288, 1369, 417]

In [6]:
tags_count['LOC']

2074

In [7]:
source_codes[2]

['mod_file_cache',
 ['/* Licensed to the Apache Software Foundation (ASF) under one or more\n',
  ' * contributor license agreements.  See the NOTICE file distributed with\n',
  ' * this work for additional information regarding copyright ownership.\n',
  ' * The ASF licenses this file to You under the Apache License, Version 2.0\n',
  ' * (the "License"); you may not use this file except in compliance with\n',
  ' * the License.  You may obtain a copy of the License at\n',
  ' *\n',
  ' *     http://www.apache.org/licenses/LICENSE-2.0\n',
  ' *\n',
  ' * Unless required by applicable law or agreed to in writing, software\n',
  ' * distributed under the License is distributed on an "AS IS" BASIS,\n',
  ' * WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.\n',
  ' * See the License for the specific language governing permissions and\n',
  ' * limitations under the License.\n',
  ' */\n',
  '\n',
  '/*\n',
  ' * Author: mod_file_cache by Bill Stoddard <stoddard apa

In [8]:
%%time
for code in source_codes :
    lines_update = []
    for i in range(1,len(code[1])+1) :
        lines_update.append([i,code[1][i-1]])
    code[1] = lines_update

Wall time: 0 ns


In [9]:
source_codes[2]

['mod_file_cache',
 [[1,
   '/* Licensed to the Apache Software Foundation (ASF) under one or more\n'],
  [2,
   ' * contributor license agreements.  See the NOTICE file distributed with\n'],
  [3,
   ' * this work for additional information regarding copyright ownership.\n'],
  [4,
   ' * The ASF licenses this file to You under the Apache License, Version 2.0\n'],
  [5,
   ' * (the "License"); you may not use this file except in compliance with\n'],
  [6, ' * the License.  You may obtain a copy of the License at\n'],
  [7, ' *\n'],
  [8, ' *     http://www.apache.org/licenses/LICENSE-2.0\n'],
  [9, ' *\n'],
  [10,
   ' * Unless required by applicable law or agreed to in writing, software\n'],
  [11,
   ' * distributed under the License is distributed on an "AS IS" BASIS,\n'],
  [12,
   ' * WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.\n'],
  [13,
   ' * See the License for the specific language governing permissions and\n'],
  [14, ' * limitations under the 

# Data Pre-Processing 

## Remove whitespace

In [10]:
%%time
for code in source_codes :
    for i in range(len(code[1])) :
        code[1][i][1] = ' '.join(code[1][i][1].split())
        code[1][i][1] = code[1][i][1].replace('\t', '')
        code[1][i][1] = code[1][i][1].replace('\n', '')
        code[1][i][1] = code[1][i][1].replace('\\n\\', '')
        code[1][i][1] = code[1][i][1].replace('\\n', '')
        code[1][i][1] = code[1][i][1].replace('\\', ' \\ ')
        code[1][i][1] = code[1][i][1].replace('/', ' / ')
        code[1][i][1] = re.sub(r"^\s+","",code[1][i][1])

Wall time: 9 ms


In [11]:
source_codes[1]

['mod_cache',
 [[1,
   '/ * Licensed to the Apache Software Foundation (ASF) under one or more'],
  [2,
   '* contributor license agreements. See the NOTICE file distributed with'],
  [3, '* this work for additional information regarding copyright ownership.'],
  [4,
   '* The ASF licenses this file to You under the Apache License, Version 2.0'],
  [5,
   '* (the "License"); you may not use this file except in compliance with'],
  [6, '* the License. You may obtain a copy of the License at'],
  [7, '*'],
  [8, '* http: /  / www.apache.org / licenses / LICENSE-2.0'],
  [9, '*'],
  [10,
   '* Unless required by applicable law or agreed to in writing, software'],
  [11, '* distributed under the License is distributed on an "AS IS" BASIS,'],
  [12,
   '* WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.'],
  [13,
   '* See the License for the specific language governing permissions and'],
  [14, '* limitations under the License.'],
  [15, '* / '],
  [16, ''],
  [17, 

## Split Codes

In [12]:
%%time
for source_code in source_codes :
    i = 0
    for baris in source_code[1] :
        if not (baris[1] == '') :
            baris[1] = word_tokenize(baris[1])
        i += 1

Wall time: 170 ms


In [13]:
source_codes[1]

['mod_cache',
 [[1,
   ['/',
    '*',
    'Licensed',
    'to',
    'the',
    'Apache',
    'Software',
    'Foundation',
    '(',
    'ASF',
    ')',
    'under',
    'one',
    'or',
    'more']],
  [2,
   ['*',
    'contributor',
    'license',
    'agreements',
    '.',
    'See',
    'the',
    'NOTICE',
    'file',
    'distributed',
    'with']],
  [3,
   ['*',
    'this',
    'work',
    'for',
    'additional',
    'information',
    'regarding',
    'copyright',
    'ownership',
    '.']],
  [4,
   ['*',
    'The',
    'ASF',
    'licenses',
    'this',
    'file',
    'to',
    'You',
    'under',
    'the',
    'Apache',
    'License',
    ',',
    'Version',
    '2.0']],
  [5,
   ['*',
    '(',
    'the',
    '``',
    'License',
    "''",
    ')',
    ';',
    'you',
    'may',
    'not',
    'use',
    'this',
    'file',
    'except',
    'in',
    'compliance',
    'with']],
  [6,
   ['*',
    'the',
    'License',
    '.',
    'You',
    'may',
    'obtain',
    'a',

## Remove Comments

### Tag Comments

In [14]:
%%time

for source_code in source_codes :
    is_comment = False
    is_comment_line = False
    baris_index = 0
    while (baris_index < len(source_code[1])) :
        word_index = 0
        while (word_index < len(source_code[1][baris_index][1])) :
            tag = 'O'
            tags_count['O'] += 1
            #print(source_code[1][baris_index][1][word_index],end=' ')
            if not(is_comment or is_comment_line) : 
                out_of_bound = (len(source_code[1][baris_index][1])-word_index <= 1)
                #print('o',end=' ')
                if not(out_of_bound) :
                    if (source_code[1][baris_index][1][word_index] == '/') and (source_code[1][baris_index][1][word_index+1] == '*') :
                        is_comment = True
                        tag = 'C'
                        tags_count['O'] -= 1
                        #print('yes1',end=' ')
                    elif (source_code[1][baris_index][1][word_index] == '/') and (source_code[1][baris_index][1][word_index+1] == '/') :
                        is_comment_line = True
                        tag = 'C'
                        tags_count['O'] -= 1
                        #print('yes2',end=' ')
            elif (is_comment or is_comment_line) :
                tag = 'C'
                tags_count['O'] -= 1
                #print('yes3',end=' ')
                if (word_index > 0) and (is_comment) :
                    #print('no1',end=' ')
                    #print(source_code[1][baris_index][1][word_index-1], source_code[1][baris_index][1][word_index])
                    if (source_code[1][baris_index][1][word_index-1][0] == '*') and (source_code[1][baris_index][1][word_index] == '/') :
                        #print('no2',end=' ')
                        if (word_index > 1) :
                            #print('no3',end=' ')
                            if not (source_code[1][baris_index][1][word_index-2][0] == '/') :
                                is_comment = False
                                #print('no',end=' ')
                        else :
                            is_comment = False
            source_code[1][baris_index][1][word_index] = [source_code[1][baris_index][1][word_index], tag]
            word_index += 1
            #print('oh')
        baris_index += 1
        is_comment_line = False

Wall time: 20 ms


In [15]:
source_codes

[['http_core',
  [[1,
    [['/', 'C'],
     ['*', 'C'],
     ['Licensed', 'C'],
     ['to', 'C'],
     ['the', 'C'],
     ['Apache', 'C'],
     ['Software', 'C'],
     ['Foundation', 'C'],
     ['(', 'C'],
     ['ASF', 'C'],
     [')', 'C'],
     ['under', 'C'],
     ['one', 'C'],
     ['or', 'C'],
     ['more', 'C']]],
   [2,
    [['*', 'C'],
     ['contributor', 'C'],
     ['license', 'C'],
     ['agreements', 'C'],
     ['.', 'C'],
     ['See', 'C'],
     ['the', 'C'],
     ['NOTICE', 'C'],
     ['file', 'C'],
     ['distributed', 'C'],
     ['with', 'C']]],
   [3,
    [['*', 'C'],
     ['this', 'C'],
     ['work', 'C'],
     ['for', 'C'],
     ['additional', 'C'],
     ['information', 'C'],
     ['regarding', 'C'],
     ['copyright', 'C'],
     ['ownership', 'C'],
     ['.', 'C']]],
   [4,
    [['*', 'C'],
     ['The', 'C'],
     ['ASF', 'C'],
     ['licenses', 'C'],
     ['this', 'C'],
     ['file', 'C'],
     ['to', 'C'],
     ['You', 'C'],
     ['under', 'C'],
     ['the', 'C'],

### Removing Comments

In [16]:
%%time

for source_code in source_codes :
    baris_index = 0
    while (baris_index < len(source_code[1])) :
        word_index = 0
        while (word_index < len(source_code[1][baris_index][1])) :
            if (source_code[1][baris_index][1][word_index][1] == 'C') :
                source_code[1][baris_index][1].pop(word_index)
                tags_count['C'] += 1
            else :
                word_index += 1
        baris_index += 1

Wall time: 0 ns


## Remove Empty Baris

In [17]:
%%time

for source_code in source_codes :
    baris_index = 0   
    while (baris_index < len(source_code[1])) :
        if len(source_code[1][baris_index][1]) <= 0 :
            source_code[1].pop(baris_index)
        else :
            baris_index += 1
    n_LOC.append(len(source_code[1]))
    tags_count['SLOC'] += len(source_code[1])

Wall time: 0 ns


In [18]:
n_LOC

[204, 806, 254]

In [19]:
tags_count['SLOC']

1264

In [20]:
source_codes[1]

['mod_cache',
 [[17, [['#', 'O'], ['define', 'O'], ['CORE_PRIVATE', 'O']]],
  [19,
   [['#', 'O'],
    ['include', 'O'],
    ['``', 'O'],
    ['mod_cache.h', 'O'],
    ["''", 'O']]],
  [21,
   [['module', 'O'],
    ['AP_MODULE_DECLARE_DATA', 'O'],
    ['cache_module', 'O'],
    [';', 'O']]],
  [22,
   [['APR_OPTIONAL_FN_TYPE', 'O'],
    ['(', 'O'],
    ['ap_cache_generate_key', 'O'],
    [')', 'O'],
    ['*', 'O'],
    ['cache_generate_key', 'O'],
    [';', 'O']]],
  [30,
   [['static', 'O'],
    ['ap_filter_rec_t', 'O'],
    ['*', 'O'],
    ['cache_save_filter_handle', 'O'],
    [';', 'O']]],
  [31,
   [['static', 'O'],
    ['ap_filter_rec_t', 'O'],
    ['*', 'O'],
    ['cache_save_subreq_filter_handle', 'O'],
    [';', 'O']]],
  [32,
   [['static', 'O'],
    ['ap_filter_rec_t', 'O'],
    ['*', 'O'],
    ['cache_out_filter_handle', 'O'],
    [';', 'O']]],
  [33,
   [['static', 'O'],
    ['ap_filter_rec_t', 'O'],
    ['*', 'O'],
    ['cache_out_subreq_filter_handle', 'O'],
    [';', 'O

# Tag Function

In [21]:
def check_is_function(source_code, index_word, index_baris, dict_function) :
    found = False #awali dengan kondisi tidak ditemukan
    
    #kondisi ketika pointer '{' merupakan urutan awal dari barisan token
    if (index_word <= 0) :
        try :
            index_baris = index_baris - 1
            index_word = len(source_code[1][index_baris][1]) - 1
        except :
            print("something went wrong, pointer can't get back to previous line")
    
    #kondisi ketika pointer '{' bukan urutan awal dari barisan
    else :
        index_word -=  1
        
    #kondisi ketika tidak menemukan token ')'
    #print('1.5',source_code[1][index_baris][1][index_word][0])
    if (not(source_code[1][index_baris][1][index_word][0] == ')')) :
        #print('why0')
        return False
    
    #cek apakah pointer berada pada baris awal dari source code
    if not(index_baris<=0) :
        #cek apakah pointer ada didalam macro
        if (source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1])-1][0]=='\\') :
            #print('why1')
            return False
    if (source_code[1][index_baris][1][0][0]=='#') :
        #print('why2')
        return False
    
    while (index_baris >= 0 and not(found)) :
        while (index_word >= 0 and not(found)) :
            #print('2',source_code[1][index_baris][1][index_word][0])
            if (source_code[1][index_baris][1][index_word][0] in stop_condition) :
                #print('why3')
                return False
            elif (source_code[1][index_baris][1][index_word][0] in (';','}')) :
                found = True;
            else :
                index_word -= 1
        if not(found) :
            index_baris = index_baris - 1
            index_word  = len(source_code[1][index_baris][1]) - 1
            
            # cek apakah baris macro
            #print('3',source_code[1][index_baris][1][index_word][0])
            if not(index_baris<=0) :
            #cek apakah pointer ada didalam macro
                #print('4',source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1])-1][0])
                if (source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1])-1][0]=='\\') :
                    found = True
            if (source_code[1][index_baris][1][0][0]=='#') :
                found = True

    if (len(source_code[1][index_baris][1]) - index_word <= 1 ) :
        index_baris += 1
        index_word = 0
    else :
        index_word += 1
        
    count = 0
    count_on = False
    is_named = False
    lines = []
    function_name = ''
    file_name = ''
    
    while (index_baris < len(source_code[1]) and (count>0 or not count_on)) :
        index_word = 0
        lines_temp = []
        lines_temp.append(source_code[1][index_baris][0])
        while (index_word < len(source_code[1][index_baris][1]) and (count>0 or not count_on)) :
            #print('g',source_code[1][index_baris][1][index_word])
            #print(index_baris)
            source_code[1][index_baris][1][index_word][1] = 'M'
            tags_count['M'] += 1
            tags_count['O'] -= 1
            lines_temp.append(source_code[1][index_baris][1][index_word][0])
            if (source_code[1][index_baris][1][index_word][0] == '{') :
                #print('yes0')
                count_on = True
                count += 1
            elif (not(is_named) and source_code[1][index_baris][1][index_word][0] == '(') :
                #print('yes1')
                if (index_word <= 0) :
                    #print('yes2')
                    source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1]) - 1][1] = 'N'
                    tags_count['M'] -= 1
                    tags_count['N'] += 1
                    function_name = source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1]) - 1][0]
                else :
                    #print('yes3')
                    source_code[1][index_baris][1][index_word-1][1] = 'N'
                    tags_count['M'] -= 1
                    tags_count['N'] += 1
                    function_name = source_code[1][index_baris][1][index_word-1][0]
                file_name = source_code[0]
                dict_function[file_name][function_name] = {}
                is_named = True
            elif (source_code[1][index_baris][1][index_word][0] == '}') :
                #print('yes4')
                count -= 1
            if (count>0 or not(count_on)) :
                index_word += 1
            #print(index_word < len(source_code[1][index_baris][1]) and (count>0 or not count_on))
        #print('final')
        lines.append(lines_temp)
        if (count>0 or not(count_on)) :
            index_baris += 1
    dict_function[file_name][function_name]['code'] = {}
    for line in lines :
        dict_function[file_name][function_name]['code'][line[0]] = []
        index = 1
        while (index<len(line)) :
            dict_function[file_name][function_name]['code'][line[0]].append(line[index])
            index += 1
    return True

In [22]:
%%time
jumlah = 0

for source_code in source_codes :
    baris_index = 0
    while (baris_index < len(source_code[1])) :
        word_index = 0
        while (word_index < len(source_code[1][baris_index][1])) :
            #print(baris_index,word_index)
            if not(source_code[1][baris_index][1][word_index][1] in ('M','N')) :    
                if (source_code[1][baris_index][1][word_index][0] == '{') :
                    if (check_is_function(source_code, word_index, baris_index,function_dict)) :
                        jumlah += 1
            word_index += 1
        baris_index += 1
#print('Jumlah :',jumlah)

Wall time: 20 ms


In [23]:
tags_count['M']

7151

In [24]:
tags_count['N']

40

In [25]:
tags_count['O']

871

In [26]:
tags_count['C']

5316

In [27]:
tags_count['all'] = tags_count['M'] + tags_count['N'] + tags_count['O'] + tags_count['C']
tags_count['all']

13378

In [28]:
source_codes[2]

['mod_file_cache',
 [[71,
   [['#', 'O'], ['include', 'O'], ['``', 'O'], ['apr.h', 'O'], ["''", 'O']]],
  [73,
   [['#', 'O'],
    ['if', 'O'],
    ['!', 'O'],
    ['(', 'O'],
    ['APR_HAS_SENDFILE', 'O'],
    ['||', 'O'],
    ['APR_HAS_MMAP', 'O'],
    [')', 'O']]],
  [74,
   [['#', 'O'],
    ['error', 'O'],
    ['mod_file_cache', 'O'],
    ['only', 'O'],
    ['works', 'O'],
    ['on', 'O'],
    ['systems', 'O'],
    ['with', 'O'],
    ['APR_HAS_SENDFILE', 'O'],
    ['or', 'O'],
    ['APR_HAS_MMAP', 'O']]],
  [75, [['#', 'O'], ['endif', 'O']]],
  [77,
   [['#', 'O'],
    ['include', 'O'],
    ['``', 'O'],
    ['apr_mmap.h', 'O'],
    ["''", 'O']]],
  [78,
   [['#', 'O'],
    ['include', 'O'],
    ['``', 'O'],
    ['apr_strings.h', 'O'],
    ["''", 'O']]],
  [79,
   [['#', 'O'],
    ['include', 'O'],
    ['``', 'O'],
    ['apr_hash.h', 'O'],
    ["''", 'O']]],
  [80,
   [['#', 'O'],
    ['include', 'O'],
    ['``', 'O'],
    ['apr_buckets.h', 'O'],
    ["''", 'O']]],
  [82, [['#', 'O'

# Tokenization

In [29]:
syntax = ('for', 'while', 'case', 'if', 'do', 'else', 'break', 'continue', 'switch', 'goto', 'return')

def give_token(x) : 
    if x == 'for' :
        return 'A'
    elif x == 'break' :
        return 'B'
    elif x == 'case' :
        return 'C'
    elif x == 'do' :
        return 'D'
    elif x == 'else' :
        return 'E'
    elif x == 'continue' :
        return 'F'
    elif x == 'goto' :
        return 'G'
    elif x == 'while' :
        return 'H'
    elif x == 'if' :
        return 'I'
    elif x == 'switch' :
        return 'J'
    elif x == 'return' :
        return 'K'
    else :
        return False

In [30]:
%%time

is_in_comment1 = False
is_in_comment2 = False
is_in_comment3 = False
is_comment = False
dummy = {}
for file in list(function_dict) :
    for function in list(function_dict[file]) :
        dummy[function] = {}
        dummy[function]['token'] = ''
        for baris in list(function_dict[file][function]['code']) :
            for token in list(function_dict[file][function]['code'][baris]) :
                if (token == '"' and not(is_in_comment2) and not(is_in_comment3)) :
                    if not(is_in_comment1) : 
                        dummy[function]['token'] += 'T'
                        is_comment = not(is_comment)
                    is_in_comment1 = not(is_in_comment1)
                elif (token == "'" and not(is_in_comment1) and not(is_in_comment3)) :
                    if not(is_in_comment2) : 
                        dummy[function]['token'] += 'T'
                        is_comment = not(is_comment)
                    is_in_comment2 = not(is_in_comment2)
                elif ((token == "``" or token == "''") and not(is_in_comment1) and not(is_in_comment2)) :
                    if not(is_in_comment3) :
                        dummy[function]['token'] += 'T'
                        is_comment = not(is_comment)
                    is_in_comment3 = not(is_in_comment3)
                if (not(is_in_comment1 or is_in_comment2 or is_in_comment3 or is_comment)) :
                    if (re.search(r'^-[\w._]+$',token)) :
                        #print('1',re.findall(r'^-[\w._]+$',token)[0])
                        if (re.findall(r'[\w._]+$',token)[0] in syntax) :
                            dummy[function]['token'] += '-'
                            if not (give_token(re.findall(r'[\w._]+$',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'[\w._]+$',token)[0]))
                            dummy[function]['token'] += give_token(re.findall(r'[\w._]+$',token)[0])
                        else :
                            dummy[function]['token'] += 'T'
                    elif (re.search(r'^[\w._]+[^\w._]+$',token)) :
                        #print('2',re.findall(r'^[\w._]+[^\w._]+$',token)[0])
                        if (re.findall(r'^[\w._]+',token)[0] in syntax) :
                            if not (give_token(re.findall(r'^[\w._]+',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'^[\w._]+',token)[0]))
                            dummy[function]['token'] += give_token(re.findall(r'^[\w._]+',token)[0])
                        else :
                            dummy[function]['token'] += 'T'
                        dummy[function]['token'] += re.findall(r'[^\w._]+$',token)[0]
                    elif (re.search(r'^[^\w._]+[\w._]+$',token)) :
                        #print('3',re.findall(r'^[^\w._]+[\w._]+$',token)[0])
                        dummy[function]['token'] += re.findall(r'^[^\w._]+',token)[0]
                        if (re.findall(r'[\w._]+$',token)[0] in syntax) :
                            if not (give_token(re.findall(r'[\w._]+$',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'[\w._]+$',token)[0]))
                            dummy[function]['token'] += give_token(re.findall(r'[\w._]+$',token)[0])
                        else :
                            dummy[function]['token'] += 'T'
                    elif(re.search(r'^[\w.]+[^\w.]+[\w.]+$',token)) :
                        #print('4',re.findall(r'^[\w.]+[^\w.]+[\w.]+$',token)[0])
                        if (re.findall(r'^[\w._]+',token)[0] in syntax) :
                            if not (give_token(re.findall(r'^[\w._]+',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'^[\w._]+',token)[0]))
                            dummy[function]['token'] += give_token(re.findall(r'^[\w._]+',token)[0])
                        else :
                            dummy[function]['token'] += 'T'
                        dummy[function]['token'] += re.findall(r'[^\w._]+',token)[0]
                        if (re.findall(r'[\w._]+$',token)[0] in syntax) :
                            if not (give_token(re.findall(r'[\w._]+$',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'[\w._]+$',token)[0]))
                            dummy[function]['token'] += give_token(re.findall(r'[\w._]+$',token)[0])
                        else :
                            dummy[function]['token'] += 'T'
                    elif (re.search(r'^[\w._]+$',token)) :
                        #print('5',re.findall(r'^[\w._]+$',token)[0])
                        if (re.findall(r'^[\w._]+$',token)[0] in syntax) :
                            if not (give_token(re.findall(r'^[\w._]+$',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'^[\w._]+$',token)[0]))
                            dummy[function]['token'] += give_token(re.findall(r'^[\w._]+$',token)[0])
                        else :
                            #print('why :',re.findall(r'^[\w._]+$',token)[0])
                            dummy[function]['token'] += 'T'
                    else :
                        dummy[function]['token'] += token
                elif (not(is_in_comment1 or is_in_comment2 or is_in_comment3)) :
                    is_comment = not(is_comment)
                    
for file in list(function_dict) :
    for function in list(function_dict[file]) :
        function_dict[file][function]['token'] = dummy[function]['token']

Wall time: 34 ms


In [31]:
len(dummy)

38

In [32]:
dummy

{'set_keep_alive_timeout': {'token': 'TTT*T(T*T,T*T,TT*T){TT*T=T(T,T|T);I(T!=T){KT;}T->T->T=T(T(T));KT;}'},
 'set_keep_alive': {'token': 'TTT*T(T*T,T*T,TT*T){TT*T=T(T,T|T);I(T!=T){KT;}I(!T(T,T)||!T(T,T)){T->T->T=T;}E{T->T->T=T;}KT;}'},
 'set_keep_alive_max': {'token': 'TTT*T(T*T,T*T,TT*T){TT*T=T(T,T|T);I(T!=T){KT;}T->T->T=T(T);KT;}'},
 'http_scheme': {'token': 'TTT*T(TT*T){I(T->T->T&&(T(T->T->T,T)==T))KT;KT;}'},
 'http_port': {'token': 'TTT(TT*T){I(T->T->T&&(T(T->T->T,T)==T))KT;KT;}'},
 'ap_process_http_async_connection': {'token': 'TTT(T*T){T*T;T*T=T->T;I(T->T){KT(T);}T(T->T==T);H(T->T==T){T(T->T,T,T);I((T=T(T))){T->T=T;T(T->T,T,T);I(T->T==T)T(T);I(T)T(T->T,T);I(T->T!=T||T->T||T()){T->T=T;}EI(!T->T){T->T=T;}T(T->T);}E{T->T=T;}}KT;}'},
 'ap_process_http_connection': {'token': 'TTT(T*T){T*T;T*T=T;T(T->T,T,T);H((T=T(T))!=T){T->T=T;T(T->T,T,T);I(T->T==T)T(T);I(T)T(T->T,T);I(T->T!=T||T->T)B;T(T->T,T,T);T(T->T);I(T())B;I(!T){T=T(T->T,&T);}T(T,T,T);T(T,T->T->T);}KT;}'},
 'http_create_request

In [34]:
i = 0
for file in function_dict :
    for function in function_dict[file] :
        function_token[file+'..'+function+'()']= function_dict[file][function]['token']

# Matching

In [36]:
import textdistance as td

## Seharusnya Code Clones

In [35]:
td.hamming.normalized_similarity(function_dict['audioop']['audioop_alaw2lin']['token'],function_dict['audioop']['audioop_reverse']['token'])

KeyError: 'audioop'

In [40]:
td.levenshtein.normalized_similarity(function_dict['audioop']['audioop_alaw2lin']['token'],function_dict['audioop']['audioop_reverse']['token'])

0.7384105960264901

In [41]:
td.jaro_winkler(function_dict['audioop']['audioop_alaw2lin']['token'],function_dict['audioop']['audioop_reverse']['token'])

0.9030080509024803

In [42]:
td.ratcliff_obershelp(function_dict['audioop']['audioop_reverse']['token'],function_dict['audioop']['audioop_alaw2lin']['token'])

0.8413284132841329

## Seharusnya Bukan Code Clones

In [43]:
td.hamming.normalized_similarity(function_dict['audioop']['search']['token'],function_dict['audioop']['audioop_getsample']['token'])

0.07526881720430112

In [44]:
td.levenshtein.normalized_similarity(function_dict['audioop']['search']['token'],function_dict['audioop']['audioop_getsample']['token'])

0.23655913978494625

In [45]:
td.jaro_winkler(function_dict['audioop']['search']['token'],function_dict['audioop']['audioop_getsample']['token'])

0.6024703918713135

In [46]:
td.ratcliff_obershelp(function_dict['audioop']['search']['token'],function_dict['audioop']['audioop_getsample']['token'])

0.3236514522821577

## Compare Functions

### ratcliff_obershelp

In [37]:
%%time
i = 0
key = list(function_token)
dummy = {}
is_clone10 = []
is_clone20 = []
is_clone30 = []
is_clone40 = []
is_clone50 = []
is_clone60 = []
is_clone70 = []
is_clone80 = []
is_clone90 = []
is_clone100 = []
while i < len(function_token)-1 :
    j = i+1
    while j < len(function_token) :
        if (key[i]<=key[j]) :
            func_to_compare = key[i]+'-'+key[j]
        else :
            func_to_compare = key[j]+'-'+key[i]
        dummy[func_to_compare] = td.ratcliff_obershelp(function_token[key[i]],function_token[key[j]])
        is_clone10.append(True)
        is_clone20.append(True)
        is_clone30.append(True)
        is_clone40.append(True)
        is_clone50.append(True)
        is_clone60.append(True)
        is_clone70.append(True)
        is_clone80.append(True)
        is_clone90.append(True)
        is_clone100.append(True)
        if (dummy[func_to_compare] < 1) :
            is_clone100[-1] = False
        if (dummy[func_to_compare] < 0.9) :
            is_clone90[-1] = False
        if (dummy[func_to_compare] < 0.8) :
            is_clone80[-1] = False
        if (dummy[func_to_compare] < 0.7) :
            is_clone70[-1] = False
        if (dummy[func_to_compare] < 0.6) :
            is_clone60[-1] = False
        if (dummy[func_to_compare] < 0.5) :
            is_clone50[-1] = False    
        if (dummy[func_to_compare] < 0.4) :
            is_clone40[-1] = False
        if (dummy[func_to_compare] < 0.3) :
            is_clone30[-1] = False
        if (dummy[func_to_compare] < 0.2) :
            is_clone20[-1] = False
        if (dummy[func_to_compare] < 0.1) :
            is_clone10[-1] = False
        j += 1
    i += 1

Wall time: 7.07 s


# Format Output

In [38]:

df = pd.DataFrame(data=dummy.items(),columns=['Method','Ratio'])
df['>10%'] = pd.DataFrame(is_clone10)
df['>20%'] = pd.DataFrame(is_clone20)
df['>30%'] = pd.DataFrame(is_clone30)
df['>40%'] = pd.DataFrame(is_clone40)
df['>50%'] = pd.DataFrame(is_clone50)
df['>60%'] = pd.DataFrame(is_clone60)
df['>70%'] = pd.DataFrame(is_clone70)
df['>80%'] = pd.DataFrame(is_clone80)
df['>90%'] = pd.DataFrame(is_clone90)
df['>100%'] = pd.DataFrame(is_clone100)

#df.set_index(['Method'], inplace=True)
df

Method     Ratio   >10%  \
0    http_core..set_keep_alive()-http_core..set_kee...  0.775000   True   
1    http_core..set_keep_alive_max()-http_core..set...  0.976744   True   
2    http_core..http_scheme()-http_core..set_keep_a...  0.561404   True   
3    http_core..http_port()-http_core..set_keep_ali...  0.535714   True   
4    http_core..ap_process_http_async_connection()-...  0.349442   True   
..                                                 ...       ...    ...   
775  mod_file_cache..file_cache_handler()-mod_file_...  0.400000   True   
776  mod_file_cache..mmap_handler()-mod_file_cache....  0.000000  False   
777  mod_file_cache..file_cache_handler()-mod_file_...  0.392638   True   
778  mod_file_cache..register_hooks()-mod_file_cach...  0.000000  False   
779  mod_file_cache..file_cache_handler()-mod_file_...  0.000000  False   

      >20%   >30%   >40%   >50%   >60%   >70%   >80%   >90%  >100%  
0     True   True   True   True   True   True  False  False  False  
1     True   True   True   True   True   True   True   True  False  
2     True   True   True   True  False  False  False  False  False  
3     True   True   True   True  False  False  False  False  False  
4     True   True  False  False  False  False  False  False  False  
..     ...    ...    ...    ...    ...    ...    ...    ...    ...  
775   True   True   True  False  False  False  False  False  False  
776  False  False  False  False  False  False  False  False  False  
777   True   True  False  False  False  False  False  False  False  
778  False  False  False  False  False  False  False  False  False  
779  False  False  False  False  False  False  False  False  False  

[780 rows x 12 columns]

In [39]:
df.sort_values(['Ratio'], ascending=False, axis=0, inplace=True)
df

Method  Ratio   >10%   >20%  \
344  http_core..register_hooks()-mod_file_cache..re...    1.0   True   True   
527  mod_cache..set_cache_ignore_cachecontrol()-mod...    1.0   True   True   
528  mod_cache..set_cache_ignore_cachecontrol()-mod...    1.0   True   True   
734  mod_cache..register_hooks()-mod_file_cache..re...    1.0   True   True   
334  http_core..register_hooks()-mod_cache..registe...    1.0   True   True   
..                                                 ...    ...    ...    ...   
319  http_core..register_hooks()-mod_cache..create_...    0.0  False  False   
318  http_core..register_hooks()-mod_cache..cache_r...    0.0  False  False   
317  http_core..register_hooks()-mod_cache..cache_s...    0.0  False  False   
316  http_core..register_hooks()-mod_cache..cache_o...    0.0  False  False   
779  mod_file_cache..file_cache_handler()-mod_file_...    0.0  False  False   

      >30%   >40%   >50%   >60%   >70%   >80%   >90%  >100%  
344   True   True   True   True   True   True   True   True  
527   True   True   True   True   True   True   True   True  
528   True   True   True   True   True   True   True   True  
734   True   True   True   True   True   True   True   True  
334   True   True   True   True   True   True   True   True  
..     ...    ...    ...    ...    ...    ...    ...    ...  
319  False  False  False  False  False  False  False  False  
318  False  False  False  False  False  False  False  False  
317  False  False  False  False  False  False  False  False  
316  False  False  False  False  False  False  False  False  
779  False  False  False  False  False  False  False  False  

[780 rows x 12 columns]

In [40]:
df.index

Int64Index([344, 527, 528, 734, 334, 752, 504, 505, 506, 557,
            ...
            323, 649, 516, 321, 320, 319, 318, 317, 316, 779],
           dtype='int64', length=780)

# Comparison

In [61]:
df_py = pd.read_excel(py_directory)
df_py

Comparision  Unnamed: 1 Students  \
0    mod_cache..cache_out_filter()-http_core..set_k...         NaN      NaN   
1    mod_cache..cache_out_filter()-mod_cache..set_c...         NaN     0.25   
2    mod_cache..cache_out_filter()-http_core..ap_pr...         NaN      NaN   
3    mod_file_cache..mmap_handler()-http_core..set_...         NaN        0   
4    mod_file_cache..mmap_handler()-mod_cache..set_...         NaN      NaN   
..                                                 ...         ...      ...   
788                                                NaN         NaN      NaN   
789                                                NaN         NaN  Student   
790                                                NaN         NaN      NaN   
791                                                NaN         NaN      NaN   
792                                                NaN         NaN      NaN   

    Unnamed: 3    Expert  Nicad-30  Nicad-40  Nicad-50  MeCC_95_20  \
0          NaN       NaN       0.0       0.0       0.0         0.0   
1          NaN  No Clone       0.0       0.0       0.0         0.0   
2          NaN       NaN       0.0       0.0       0.0         0.0   
3          NaN  No Clone       0.0       0.0       0.0         0.0   
4          NaN       NaN       0.0       0.0       0.0         0.0   
..         ...       ...       ...       ...       ...         ...   
788      Total       357       NaN       NaN       NaN         NaN   
789        NaN       NaN       NaN       NaN       NaN         NaN   
790     Clones        23       NaN       NaN       NaN         NaN   
791  Not Clone       334       NaN       NaN       NaN         NaN   
792      Total       357       NaN       NaN       NaN         NaN   

     MeCC_95_10  ...  MeCC_70_10  MeCC_70_4  MeCC_60_20  MeCC_60_10  \
0           0.0  ...         0.0        0.0         0.0         0.0   
1           0.0  ...         0.0        0.0         0.0         0.0   
2           0.0  ...         0.0        0.0         0.0         0.0   
3           0.0  ...         0.0        1.0         0.0         0.0   
4           0.0  ...         0.0        1.0         0.0         0.0   
..          ...  ...         ...        ...         ...         ...   
788         NaN  ...         NaN        NaN         NaN         NaN   
789         NaN  ...         NaN        NaN         NaN         NaN   
790         NaN  ...         NaN        NaN         NaN         NaN   
791         NaN  ...         NaN        NaN         NaN         NaN   
792         NaN  ...         NaN        NaN         NaN         NaN   

     MeCC_60_4  MeCC_50_20  MeCC_50_10  MeCC_50_4  SimCad  CCCD-30  
0          0.0         0.0         0.0        0.0     0.0      0.0  
1          0.0         0.0         0.0        0.0     0.0      0.0  
2          0.0         0.0         0.0        0.0     0.0      0.0  
3          1.0         0.0         1.0        1.0     0.0      0.0  
4          1.0         0.0         1.0        1.0     0.0      0.0  
..         ...         ...         ...        ...     ...      ...  
788        NaN         NaN         NaN        NaN     NaN      NaN  
789        NaN         NaN         NaN        NaN     NaN      NaN  
790        NaN         NaN         NaN        NaN     NaN      NaN  
791        NaN         NaN         NaN        NaN     NaN      NaN  
792        NaN         NaN         NaN        NaN     NaN      NaN  

[793 rows x 28 columns]

In [62]:
df_py = df_py.dropna(subset=['Expert', 'Students'])
df_py

Comparision  Unnamed: 1 Students  \
1    mod_cache..cache_out_filter()-mod_cache..set_c...         NaN     0.25   
3    mod_file_cache..mmap_handler()-http_core..set_...         NaN        0   
5    mod_file_cache..mmap_handler()-http_core..ap_p...         NaN        0   
7    mod_cache..add_cache_disable()-http_core..set_...         NaN        0   
9    mod_cache..add_cache_disable()-http_core..ap_p...         NaN        0   
..                                                 ...         ...      ...   
770  mod_file_cache..cache_the_file()-mod_file_cach...         NaN        0   
772  mod_file_cache..cache_the_file()-mod_file_cach...         NaN        0   
774  mod_file_cache..cache_the_file()-http_core..re...         NaN        0   
776  mod_file_cache..cache_the_file()-mod_cache..se...         NaN     0.25   
779                                       Total Clones         NaN       23   

    Unnamed: 3          Expert  Nicad-30  Nicad-40  Nicad-50  MeCC_95_20  \
1          NaN        No Clone       0.0       0.0       0.0         0.0   
3          NaN        No Clone       0.0       0.0       0.0         0.0   
5          NaN        No Clone       0.0       0.0       0.0         0.0   
7          NaN        No Clone       0.0       0.0       0.0         0.0   
9          NaN        No Clone       0.0       0.0       0.0         0.0   
..         ...             ...       ...       ...       ...         ...   
770        NaN        No Clone       0.0       0.0       0.0         0.0   
772        NaN        No Clone       0.0       0.0       0.0         0.0   
774        NaN        No Clone       0.0       0.0       0.0         0.0   
776        NaN  Not Classified       0.0       0.0       0.0         0.0   
779        NaN              18       1.0       5.0      28.0         2.0   

     MeCC_95_10  ...  MeCC_70_10  MeCC_70_4  MeCC_60_20  MeCC_60_10  \
1           0.0  ...         0.0        0.0         0.0         0.0   
3           0.0  ...         0.0        1.0         0.0         0.0   
5           0.0  ...         0.0        1.0         1.0         1.0   
7           0.0  ...         0.0        1.0         0.0         1.0   
9           0.0  ...         0.0        1.0         0.0         1.0   
..          ...  ...         ...        ...         ...         ...   
770         0.0  ...         0.0        1.0         0.0         1.0   
772         0.0  ...         0.0        1.0         0.0         1.0   
774         0.0  ...         0.0        0.0         0.0         0.0   
776         0.0  ...         0.0        1.0         0.0         1.0   
779        14.0  ...        99.0      406.0       117.0       303.0   

     MeCC_60_4  MeCC_50_20  MeCC_50_10  MeCC_50_4  SimCad  CCCD-30  
1          0.0         0.0         0.0        0.0     0.0      0.0  
3          1.0         0.0         1.0        1.0     0.0      0.0  
5          1.0         1.0         1.0        1.0     0.0      0.0  
7          1.0         1.0         1.0        1.0     1.0      0.0  
9          1.0         1.0         1.0        1.0     0.0      0.0  
..         ...         ...         ...        ...     ...      ...  
770        1.0         1.0         1.0        1.0     0.0      0.0  
772        1.0         1.0         1.0        1.0     0.0      0.0  
774        0.0         0.0         0.0        0.0     0.0      0.0  
776        1.0         1.0         1.0        1.0     0.0      0.0  
779      578.0       302.0       488.0      613.0    18.0      NaN  

[356 rows x 28 columns]

In [58]:
df_py['Expert'].unique()

array(['No Clone', 'Type 2', 'Not Classified', 18], dtype=object)

In [69]:
for i in range(1,len(df_py.index)) :
    if (df_py.index[i]-df_py.index[i-1] > 4):
        print(df_py.index[i])

319
473
652
718
758


In [59]:
#df_py = df_py[df_py.Expert != 'Not Classified']
#df_py = df_py[df_py.Expert != 18]
df_py

Comparision  Unnamed: 1 Students  \
1    mod_cache..cache_out_filter()-mod_cache..set_c...         NaN     0.25   
3    mod_file_cache..mmap_handler()-http_core..set_...         NaN        0   
5    mod_file_cache..mmap_handler()-http_core..ap_p...         NaN        0   
7    mod_cache..add_cache_disable()-http_core..set_...         NaN        0   
9    mod_cache..add_cache_disable()-http_core..ap_p...         NaN        0   
..                                                 ...         ...      ...   
770  mod_file_cache..cache_the_file()-mod_file_cach...         NaN        0   
772  mod_file_cache..cache_the_file()-mod_file_cach...         NaN        0   
774  mod_file_cache..cache_the_file()-http_core..re...         NaN        0   
776  mod_file_cache..cache_the_file()-mod_cache..se...         NaN     0.25   
779                                       Total Clones         NaN       23   

    Unnamed: 3          Expert  Nicad-30  Nicad-40  Nicad-50  MeCC_95_20  \
1          NaN        No Clone       0.0       0.0       0.0         0.0   
3          NaN        No Clone       0.0       0.0       0.0         0.0   
5          NaN        No Clone       0.0       0.0       0.0         0.0   
7          NaN        No Clone       0.0       0.0       0.0         0.0   
9          NaN        No Clone       0.0       0.0       0.0         0.0   
..         ...             ...       ...       ...       ...         ...   
770        NaN        No Clone       0.0       0.0       0.0         0.0   
772        NaN        No Clone       0.0       0.0       0.0         0.0   
774        NaN        No Clone       0.0       0.0       0.0         0.0   
776        NaN  Not Classified       0.0       0.0       0.0         0.0   
779        NaN              18       1.0       5.0      28.0         2.0   

     MeCC_95_10  ...  MeCC_70_10  MeCC_70_4  MeCC_60_20  MeCC_60_10  \
1           0.0  ...         0.0        0.0         0.0         0.0   
3           0.0  ...         0.0        1.0         0.0         0.0   
5           0.0  ...         0.0        1.0         1.0         1.0   
7           0.0  ...         0.0        1.0         0.0         1.0   
9           0.0  ...         0.0        1.0         0.0         1.0   
..          ...  ...         ...        ...         ...         ...   
770         0.0  ...         0.0        1.0         0.0         1.0   
772         0.0  ...         0.0        1.0         0.0         1.0   
774         0.0  ...         0.0        0.0         0.0         0.0   
776         0.0  ...         0.0        1.0         0.0         1.0   
779        14.0  ...        99.0      406.0       117.0       303.0   

     MeCC_60_4  MeCC_50_20  MeCC_50_10  MeCC_50_4  SimCad  CCCD-30  
1          0.0         0.0         0.0        0.0     0.0      0.0  
3          1.0         0.0         1.0        1.0     0.0      0.0  
5          1.0         1.0         1.0        1.0     0.0      0.0  
7          1.0         1.0         1.0        1.0     1.0      0.0  
9          1.0         1.0         1.0        1.0     0.0      0.0  
..         ...         ...         ...        ...     ...      ...  
770        1.0         1.0         1.0        1.0     0.0      0.0  
772        1.0         1.0         1.0        1.0     0.0      0.0  
774        0.0         0.0         0.0        0.0     0.0      0.0  
776        1.0         1.0         1.0        1.0     0.0      0.0  
779      578.0       302.0       488.0      613.0    18.0      NaN  

[356 rows x 28 columns]

In [46]:
df_py = df_py.rename(columns={'Unnamed: 0':'Method'})

In [56]:
df_py = df_py[['Method','Expert']]
df_py

Method    Expert
0     grpmodule..grp_getgrgid()-audioop..audioop_lin...  No Clone
5     fcntlmodule..fcntl_fcntl()-cmathmodule..c_prodi()  No Clone
10     cmathmodule..c_asin()-audioop..audioop_lin2lin()  No Clone
15      fpetestmodule..db0()-audioop..audioop_lin2lin()  No Clone
25          audioop..audioop_cross()-fcntlmodule..ins()  No Clone
...                                                 ...       ...
2981  fpetestmodule..nest3()-fpectlmodule..initfpectl()  No Clone
2989      fpetestmodule..nest3()-audioop..initaudioop()  No Clone
2993   fpetestmodule..nest3()-fpetestmodule..printerr()  No Clone
2997        fpetestmodule..nest3()-grpmodule..mkgrent()  No Clone
3001  fpetestmodule..nest3()-audioop..audioop_lin2ad...  No Clone

[545 rows x 2 columns]

### Check if both result detected same methods

In [84]:
arr_comparable_methods = list(df_py['Method'])

arr_temp = []
for comparable_methods in arr_comparable_methods :
    temp = sorted(comparable_methods.split('-'))
    print(temp)
    arr_temp.append(temp)
arr_comparable_methods = arr_temp

['audioop..audioop_lin2lin()', 'grpmodule..grp_getgrgid()']
['cmathmodule..c_prodi()', 'fcntlmodule..fcntl_fcntl()']
['audioop..audioop_lin2lin()', 'cmathmodule..c_asin()']
['audioop..audioop_lin2lin()', 'fpetestmodule..db0()']
['audioop..audioop_cross()', 'fcntlmodule..ins()']
['cmathmodule..c_cos()', 'cmathmodule..c_prodi()']
['audioop..audioop_cross()', 'cmathmodule..c_cos()']
['audioop..audioop_lin2lin()', 'fpetestmodule..nest2()']
['cmathmodule..c_asin()', 'fpetestmodule..nest2()']
['audioop..audioop_lin2lin()', 'cmathmodule..c_atan()']
['cmathmodule..c_atan()', 'fpetestmodule..nest2()']
['fcntlmodule..ins()', 'fpectlmodule..fpe_reset()']
['audioop..search()', 'fpectlmodule..fpe_reset()']
['audioop..audioop_cross()', 'cmathmodule..cmath_log()']
['cmathmodule..cmath_log()', 'fpectlmodule..fpe_reset()']
['audioop..audioop_reverse()', 'fcntlmodule..ins()']
['audioop..audioop_reverse()', 'audioop..search()']
['audioop..audioop_tostereo()', 'cmathmodule..c_asin()']
['audioop..audioop_t

In [85]:
list0 = []
for row,col in df.iterrows() :
    for method in list(col['Method']) :
        print(method)
        if (method in list0) :
            print('no')
        else :
            list0.append(method)
            print('yes')

a
yes
u
yes
d
yes
i
yes
o
yes
o
no
p
yes
.
yes
.
no
a
no
u
no
d
no
i
no
o
no
o
no
p
no
_
yes
a
no
l
yes
a
no
w
yes
2
yes
l
no
i
no
n
yes
(
yes
)
yes
-
yes
a
no
u
no
d
no
i
no
o
no
o
no
p
no
.
no
.
no
a
no
u
no
d
no
i
no
o
no
o
no
p
no
_
no
u
no
l
no
a
no
w
no
2
no
l
no
i
no
n
no
(
no
)
no
c
yes
m
yes
a
no
t
yes
h
yes
m
no
o
no
d
no
u
no
l
no
e
yes
.
no
.
no
c
no
_
no
a
no
c
no
o
no
s
yes
h
no
(
no
)
no
-
no
c
no
m
no
a
no
t
no
h
no
m
no
o
no
d
no
u
no
l
no
e
no
.
no
.
no
c
no
_
no
a
no
s
no
i
no
n
no
h
no
(
no
)
no
c
no
m
no
a
no
t
no
h
no
m
no
o
no
d
no
u
no
l
no
e
no
.
no
.
no
c
no
_
no
c
no
o
no
s
no
h
no
(
no
)
no
-
no
c
no
m
no
a
no
t
no
h
no
m
no
o
no
d
no
u
no
l
no
e
no
.
no
.
no
c
no
_
no
s
no
i
no
n
no
h
no
(
no
)
no
a
no
u
no
d
no
i
no
o
no
o
no
p
no
.
no
.
no
a
no
u
no
d
no
i
no
o
no
o
no
p
no
_
no
l
no
i
no
n
no
2
no
a
no
l
no
a
no
w
no
(
no
)
no
-
no
a
no
u
no
d
no
i
no
o
no
o
no
p
no
.
no
.
no
a
no
u
no
d
no
i
no
o
no
o
no
p
no
_
no
l
no
i
no
n
no
2
no
u
no
l
no
a
no
w
no

In [66]:
list1 = []
for comparable_methods in arr_comparable_methods :
    for method in comparable_methods :
        print(method)
        if (method in list1) :
            print('no')
        else :
            list1.append(method)
            print('yes')

audioop..audioop_lin2lin()
yes
grpmodule..grp_getgrgid()
yes
cmathmodule..c_prodi()
yes
fcntlmodule..fcntl_fcntl()
yes
audioop..audioop_lin2lin()
no
cmathmodule..c_asin()
yes
audioop..audioop_lin2lin()
no
fpetestmodule..db0()
yes
audioop..audioop_cross()
yes
fcntlmodule..ins()
yes
cmathmodule..c_cos()
yes
cmathmodule..c_prodi()
no
audioop..audioop_cross()
no
cmathmodule..c_cos()
no
audioop..audioop_lin2lin()
no
fpetestmodule..nest2()
yes
cmathmodule..c_asin()
no
fpetestmodule..nest2()
no
audioop..audioop_lin2lin()
no
cmathmodule..c_atan()
yes
cmathmodule..c_atan()
no
fpetestmodule..nest2()
no
fcntlmodule..ins()
no
fpectlmodule..fpe_reset()
yes
audioop..search()
yes
fpectlmodule..fpe_reset()
no
audioop..audioop_cross()
no
cmathmodule..cmath_log()
yes
cmathmodule..cmath_log()
no
fpectlmodule..fpe_reset()
no
audioop..audioop_reverse()
yes
fcntlmodule..ins()
no
audioop..audioop_reverse()
no
audioop..search()
no
audioop..audioop_tostereo()
yes
cmathmodule..c_asin()
no
audioop..audioop_toste

#### Check if there are any differences

In [67]:
len(set(list1).difference(set(list0)))

0

#### Get all the comparable method

In [57]:
for row in df_py['Method'] :
    key=row.split('-')
    if (key[0]<=key[1]) :
        new_key = key[0]+'-'+key[1]
    else :
        new_key = key[1]+'-'+key[0]
    df_py=df_py.replace(to_replace=row, value=new_key)

In [58]:
df_py=df_py.set_index('Method')
df_py

Expert
Method                                                      
audioop..audioop_lin2lin()-grpmodule..grp_getgr...  No Clone
cmathmodule..c_prodi()-fcntlmodule..fcntl_fcntl()   No Clone
audioop..audioop_lin2lin()-cmathmodule..c_asin()    No Clone
audioop..audioop_lin2lin()-fpetestmodule..db0()     No Clone
audioop..audioop_cross()-fcntlmodule..ins()         No Clone
...                                                      ...
fpectlmodule..initfpectl()-fpetestmodule..nest3()   No Clone
audioop..initaudioop()-fpetestmodule..nest3()       No Clone
fpetestmodule..nest3()-fpetestmodule..printerr()    No Clone
fpetestmodule..nest3()-grpmodule..mkgrent()         No Clone
audioop..audioop_lin2adpcm()-fpetestmodule..nes...  No Clone

[545 rows x 1 columns]

In [59]:
df = df.set_index('Method')

In [60]:
df

Ratio   >10%   >20%  \
Method                                                                       
audioop..audioop_alaw2lin()-audioop..audioop_ul...  1.000000   True   True   
cmathmodule..c_acosh()-cmathmodule..c_asinh()       1.000000   True   True   
cmathmodule..c_cosh()-cmathmodule..c_sinh()         1.000000   True   True   
audioop..audioop_lin2alaw()-audioop..audioop_li...  1.000000   True   True   
cmathmodule..c_cos()-cmathmodule..c_sinh()          1.000000   True   True   
...                                                      ...    ...    ...   
fcntlmodule..all_ins()-grpmodule..initgrp()         0.046125  False  False   
audioop..search()-fcntlmodule..all_ins()            0.045028  False  False   
audioop..audioop_ratecv()-cmathmodule..c_prodi()    0.042831  False  False   
cmathmodule..c_prodi()-fcntlmodule..all_ins()       0.040619  False  False   
fcntlmodule..all_ins()-fpectlmodule..sigfpe_han...  0.036329  False  False   

                                                     >30%   >40%   >50%  \
Method                                                                    
audioop..audioop_alaw2lin()-audioop..audioop_ul...   True   True   True   
cmathmodule..c_acosh()-cmathmodule..c_asinh()        True   True   True   
cmathmodule..c_cosh()-cmathmodule..c_sinh()          True   True   True   
audioop..audioop_lin2alaw()-audioop..audioop_li...   True   True   True   
cmathmodule..c_cos()-cmathmodule..c_sinh()           True   True   True   
...                                                   ...    ...    ...   
fcntlmodule..all_ins()-grpmodule..initgrp()         False  False  False   
audioop..search()-fcntlmodule..all_ins()            False  False  False   
audioop..audioop_ratecv()-cmathmodule..c_prodi()    False  False  False   
cmathmodule..c_prodi()-fcntlmodule..all_ins()       False  False  False   
fcntlmodule..all_ins()-fpectlmodule..sigfpe_han...  False  False  False   

                                                     >60%   >70%   >80%  \
Method                                                                    
audioop..audioop_alaw2lin()-audioop..audioop_ul...   True   True   True   
cmathmodule..c_acosh()-cmathmodule..c_asinh()        True   True   True   
cmathmodule..c_cosh()-cmathmodule..c_sinh()          True   True   True   
audioop..audioop_lin2alaw()-audioop..audioop_li...   True   True   True   
cmathmodule..c_cos()-cmathmodule..c_sinh()           True   True   True   
...                                                   ...    ...    ...   
fcntlmodule..all_ins()-grpmodule..initgrp()         False  False  False   
audioop..search()-fcntlmodule..all_ins()            False  False  False   
audioop..audioop_ratecv()-cmathmodule..c_prodi()    False  False  False   
cmathmodule..c_prodi()-fcntlmodule..all_ins()       False  False  False   
fcntlmodule..all_ins()-fpectlmodule..sigfpe_han...  False  False  False   

                                                     >90%  >100%  
Method                                                            
audioop..audioop_alaw2lin()-audioop..audioop_ul...   True   True  
cmathmodule..c_acosh()-cmathmodule..c_asinh()        True   True  
cmathmodule..c_cosh()-cmathmodule..c_sinh()          True   True  
audioop..audioop_lin2alaw()-audioop..audioop_li...   True   True  
cmathmodule..c_cos()-cmathmodule..c_sinh()           True   True  
...                                                   ...    ...  
fcntlmodule..all_ins()-grpmodule..initgrp()         False  False  
audioop..search()-fcntlmodule..all_ins()            False  False  
audioop..audioop_ratecv()-cmathmodule..c_prodi()    False  False  
cmathmodule..c_prodi()-fcntlmodule..all_ins()       False  False  
fcntlmodule..all_ins()-fpectlmodule..sigfpe_han...  False  False  

[3003 rows x 11 columns]

In [62]:
df_final=pd.concat([df, df_py], axis=1)
df_final = df_final.dropna(subset=['Expert'])
df_final['Expert'] = df_final['Expert'].replace(to_replace=r'^No Clone$', value= False, regex=True)
df_final['Expert'] = df_final['Expert'].replace(to_replace=r'^Type.*$', value= True, regex=True)
df_final['Expert'] = df_final['Expert'].replace(to_replace=r'^type.*$', value= True, regex=True)
df_final

Ratio   >10%   >20%  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()   0.949939   True   True   
audioop..audioop_avg()-audioop..audioop_minmax()    0.920097   True   True   
audioop..audioop_max()-audioop..audioop_rms()       0.908654   True   True   
audioop..audioop_avg()-audioop..audioop_max()       0.904177   True   True   
audioop..audioop_mul()-audioop..audioop_tomono()    0.878866   True   True   
...                                                      ...    ...    ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     0.071560  False  False   
cmathmodule..c_acos()-fcntlmodule..all_ins()        0.070142  False  False   
cmathmodule..math_error()-fcntlmodule..all_ins()    0.069943  False  False   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  0.067890  False  False   
fcntlmodule..all_ins()-fcntlmodule..ins()           0.061972  False  False   

                                                     >30%   >40%   >50%  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()    True   True   True   
audioop..audioop_avg()-audioop..audioop_minmax()     True   True   True   
audioop..audioop_max()-audioop..audioop_rms()        True   True   True   
audioop..audioop_avg()-audioop..audioop_max()        True   True   True   
audioop..audioop_mul()-audioop..audioop_tomono()     True   True   True   
...                                                   ...    ...    ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     False  False  False   
cmathmodule..c_acos()-fcntlmodule..all_ins()        False  False  False   
cmathmodule..math_error()-fcntlmodule..all_ins()    False  False  False   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  False  False  False   
fcntlmodule..all_ins()-fcntlmodule..ins()           False  False  False   

                                                     >60%   >70%   >80%  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()    True   True   True   
audioop..audioop_avg()-audioop..audioop_minmax()     True   True   True   
audioop..audioop_max()-audioop..audioop_rms()        True   True   True   
audioop..audioop_avg()-audioop..audioop_max()        True   True   True   
audioop..audioop_mul()-audioop..audioop_tomono()     True   True   True   
...                                                   ...    ...    ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     False  False  False   
cmathmodule..c_acos()-fcntlmodule..all_ins()        False  False  False   
cmathmodule..math_error()-fcntlmodule..all_ins()    False  False  False   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  False  False  False   
fcntlmodule..all_ins()-fcntlmodule..ins()           False  False  False   

                                                     >90%  >100%  Expert  
audioop..audioop_avgpp()-audioop..audioop_maxpp()    True  False    True  
audioop..audioop_avg()-audioop..audioop_minmax()     True  False    True  
audioop..audioop_max()-audioop..audioop_rms()        True  False    True  
audioop..audioop_avg()-audioop..audioop_max()        True  False    True  
audioop..audioop_mul()-audioop..audioop_tomono()    False  False    True  
...                                                   ...    ...     ...  
audioop..audioop_ratecv()-cmathmodule..c_sinh()     False  False   False  
cmathmodule..c_acos()-fcntlmodule..all_ins()        False  False   False  
cmathmodule..math_error()-fcntlmodule..all_ins()    False  False   False  
audioop..audioop_ratecv()-fcntlmodule..conv_des...  False  False   False  
fcntlmodule..all_ins()-fcntlmodule..ins()           False  False   False  

[545 rows x 12 columns]

In [116]:
for ratio in ['>10%','>20%','>30%','>40%','>50%','>60%','>70%','>80%','>90%','>100%'] :
    comparison_column = np.where((df_final[ratio] == df_final['Expert']) , True, False)
    df_final[ratio+' Result'] = comparison_column

In [117]:
df_final

Ratio   >10%   >20%  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()   0.949939   True   True   
audioop..audioop_avg()-audioop..audioop_minmax()    0.920097   True   True   
audioop..audioop_max()-audioop..audioop_rms()       0.908654   True   True   
audioop..audioop_avg()-audioop..audioop_max()       0.904177   True   True   
audioop..audioop_mul()-audioop..audioop_tomono()    0.878866   True   True   
...                                                      ...    ...    ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     0.071560  False  False   
cmathmodule..c_acos()-fcntlmodule..all_ins()        0.070142  False  False   
cmathmodule..math_error()-fcntlmodule..all_ins()    0.069943  False  False   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  0.067890  False  False   
fcntlmodule..all_ins()-fcntlmodule..ins()           0.061972  False  False   

                                                     >30%   >40%   >50%  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()    True   True   True   
audioop..audioop_avg()-audioop..audioop_minmax()     True   True   True   
audioop..audioop_max()-audioop..audioop_rms()        True   True   True   
audioop..audioop_avg()-audioop..audioop_max()        True   True   True   
audioop..audioop_mul()-audioop..audioop_tomono()     True   True   True   
...                                                   ...    ...    ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     False  False  False   
cmathmodule..c_acos()-fcntlmodule..all_ins()        False  False  False   
cmathmodule..math_error()-fcntlmodule..all_ins()    False  False  False   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  False  False  False   
fcntlmodule..all_ins()-fcntlmodule..ins()           False  False  False   

                                                     >60%   >70%   >80%  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()    True   True   True   
audioop..audioop_avg()-audioop..audioop_minmax()     True   True   True   
audioop..audioop_max()-audioop..audioop_rms()        True   True   True   
audioop..audioop_avg()-audioop..audioop_max()        True   True   True   
audioop..audioop_mul()-audioop..audioop_tomono()     True   True   True   
...                                                   ...    ...    ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     False  False  False   
cmathmodule..c_acos()-fcntlmodule..all_ins()        False  False  False   
cmathmodule..math_error()-fcntlmodule..all_ins()    False  False  False   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  False  False  False   
fcntlmodule..all_ins()-fcntlmodule..ins()           False  False  False   

                                                     >90%  ...  >10% Result  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()    True  ...         True   
audioop..audioop_avg()-audioop..audioop_minmax()     True  ...         True   
audioop..audioop_max()-audioop..audioop_rms()        True  ...         True   
audioop..audioop_avg()-audioop..audioop_max()        True  ...         True   
audioop..audioop_mul()-audioop..audioop_tomono()    False  ...         True   
...                                                   ...  ...          ...   
audioop..audioop_ratecv()-cmathmodule..c_sinh()     False  ...         True   
cmathmodule..c_acos()-fcntlmodule..all_ins()        False  ...         True   
cmathmodule..math_error()-fcntlmodule..all_ins()    False  ...         True   
audioop..audioop_ratecv()-fcntlmodule..conv_des...  False  ...         True   
fcntlmodule..all_ins()-fcntlmodule..ins()           False  ...         True   

                                                   >20% Result  >30% Result  \
audioop..audioop_avgpp()-audioop..audioop_maxpp()         True         True   
audioop..audioop_avg()-audioop..audioop_minmax()          True         True   
audioop..audioop_max()-audioop..audioop_rms()             True         True   
audioop..audioop_avg()-audioop..audioop_max()      

In [89]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>10%'], rownames=['Actual'], colnames=['Predicted'])
print(">10% Accuracy :",accuracy_score(df_final['Expert'],df_final['>10%']))
print(">10% Precision :",precision_score(df_final['Expert'],df_final['>10%']))
print(">10% Recall :",recall_score(df_final['Expert'],df_final['>10%']))
print(">10% F1 :",f1_score(df_final['Expert'],df_final['>10%']))
confusion_matrix

>10% Accuracy : 0.05504587155963303
>10% Precision : 0.02830188679245283
>10% Recall : 1.0
>10% F1 : 0.055045871559633024


Predicted  False  True 
Actual                 
False         15    515
True           0     15

In [90]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>20%'], rownames=['Actual'], colnames=['Predicted'])
print(">20% Accuracy :",accuracy_score(df_final['Expert'],df_final['>20%']))
print(">20% Precision :",precision_score(df_final['Expert'],df_final['>20%']))
print(">20% Recall :",recall_score(df_final['Expert'],df_final['>20%']))
print(">20% F1 :",f1_score(df_final['Expert'],df_final['>20%']))
confusion_matrix

>20% Accuracy : 0.24036697247706423
>20% Precision : 0.03496503496503497
>20% Recall : 1.0
>20% F1 : 0.06756756756756757


Predicted  False  True 
Actual                 
False        116    414
True           0     15

In [91]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>30%'], rownames=['Actual'], colnames=['Predicted'])
print(">30% Accuracy :",accuracy_score(df_final['Expert'],df_final['>30%']))
print(">30% Precision :",precision_score(df_final['Expert'],df_final['>30%']))
print(">30% Recall :",recall_score(df_final['Expert'],df_final['>30%']))
print(">30% F1 :",f1_score(df_final['Expert'],df_final['>30%']))
confusion_matrix

>30% Accuracy : 0.43853211009174314
>30% Precision : 0.04672897196261682
>30% Recall : 1.0
>30% F1 : 0.08928571428571429


Predicted  False  True 
Actual                 
False        224    306
True           0     15

In [92]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>40%'], rownames=['Actual'], colnames=['Predicted'])
print(">40% Accuracy :",accuracy_score(df_final['Expert'],df_final['>40%']))
print(">40% Precision :",precision_score(df_final['Expert'],df_final['>40%']))
print(">40% Recall :",recall_score(df_final['Expert'],df_final['>40%']))
print(">40% F1 :",f1_score(df_final['Expert'],df_final['>40%']))
confusion_matrix

>40% Accuracy : 0.6513761467889908
>40% Precision : 0.07317073170731707
>40% Recall : 1.0
>40% F1 : 0.13636363636363635


Predicted  False  True 
Actual                 
False        340    190
True           0     15

In [93]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>50%'], rownames=['Actual'], colnames=['Predicted'])
print(">50% Accuracy :",accuracy_score(df_final['Expert'],df_final['>50%']))
print(">50% Precision :",precision_score(df_final['Expert'],df_final['>50%']))
print(">50% Recall :",recall_score(df_final['Expert'],df_final['>50%']))
print(">50% F1 :",f1_score(df_final['Expert'],df_final['>50%']))
confusion_matrix

>50% Accuracy : 0.8091743119266055
>50% Precision : 0.12605042016806722
>50% Recall : 1.0
>50% F1 : 0.22388059701492538


Predicted  False  True 
Actual                 
False        426    104
True           0     15

In [95]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>60%'], rownames=['Actual'], colnames=['Predicted'])
print(">60% Accuracy :",accuracy_score(df_final['Expert'],df_final['>60%']))
print(">60% Precision :",precision_score(df_final['Expert'],df_final['>60%']))
print(">60% Recall :",recall_score(df_final['Expert'],df_final['>60%']))
print(">60% F1 :",f1_score(df_final['Expert'],df_final['>60%']))
confusion_matrix

>60% Accuracy : 0.9119266055045872
>60% Precision : 0.23809523809523808
>60% Recall : 1.0
>60% F1 : 0.3846153846153846


Predicted  False  True 
Actual                 
False        482     48
True           0     15

In [96]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>70%'], rownames=['Actual'], colnames=['Predicted'])
print(">70% Accuracy :",accuracy_score(df_final['Expert'],df_final['>70%']))
print(">70% Precision :",precision_score(df_final['Expert'],df_final['>70%']))
print(">70% Recall :",recall_score(df_final['Expert'],df_final['>70%']))
print(">70% F1 :",f1_score(df_final['Expert'],df_final['>70%']))
confusion_matrix

>70% Accuracy : 0.9761467889908257
>70% Precision : 0.5357142857142857
>70% Recall : 1.0
>70% F1 : 0.6976744186046512


Predicted  False  True 
Actual                 
False        517     13
True           0     15

In [97]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>80%'], rownames=['Actual'], colnames=['Predicted'])
print(">80% Accuracy :",accuracy_score(df_final['Expert'],df_final['>80%']))
print(">80% Precision :",precision_score(df_final['Expert'],df_final['>80%']))
print(">80% Recall :",recall_score(df_final['Expert'],df_final['>80%']))
print(">80% F1 :",f1_score(df_final['Expert'],df_final['>80%']))
confusion_matrix

>80% Accuracy : 0.9944954128440368
>80% Precision : 0.9285714285714286
>80% Recall : 0.8666666666666667
>80% F1 : 0.896551724137931


Predicted  False  True 
Actual                 
False        529      1
True           2     13

In [98]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>90%'], rownames=['Actual'], colnames=['Predicted'])
print(">90% Accuracy :",accuracy_score(df_final['Expert'],df_final['>90%']))
print(">90% Precision :",precision_score(df_final['Expert'],df_final['>90%']))
print(">90% Recall :",recall_score(df_final['Expert'],df_final['>90%']))
print(">90% F1 :",f1_score(df_final['Expert'],df_final['>90%']))
confusion_matrix

>90% Accuracy : 0.9798165137614679
>90% Precision : 1.0
>90% Recall : 0.26666666666666666
>90% F1 : 0.4210526315789474


Predicted  False  True 
Actual                 
False        530      0
True          11      4

In [99]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>100%'], rownames=['Actual'], colnames=['Predicted'])
print(">100% Accuracy :",accuracy_score(df_final['Expert'],df_final['>100%']))
print(">100% Precision :",precision_score(df_final['Expert'],df_final['>100%']))
print(">100% Recall :",recall_score(df_final['Expert'],df_final['>100%']))
print(">100% F1 :",f1_score(df_final['Expert'],df_final['>100%']))
confusion_matrix

>100% Accuracy : 0.9724770642201835
>100% Precision : 0.0
>100% Recall : 0.0
>100% F1 : 0.0


C:\Users\haydariday\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1245: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Predicted  False
Actual          
False        530
True          15